# **HeartView Pipeline for Actiwave Cardio and Other ECG Sources**
## ECG Signal Quality Assessment

This notebook presents an example of the HeartView pipeline's functionalities on some sample ECG data.

### 1. Import Modules

In [67]:
from sys import path
path.append('../')
from heartview import heartview
from heartview.pipeline import ECG, SQA
import pandas as pd
import matplotlib.pyplot as plt

### 2. Load Data

#### 2-a. Load Data of Actiwave Cardio

In [68]:
edf = 'sample_actiwave.edf'
ecg, acc = ECG.read_actiwave(edf)
data = ecg
display(ecg.head(), acc.head())

Timestamp        mV
0 2023-10-03 17:28:43.000000 -0.045764
1 2023-10-03 17:28:43.000977 -0.050443
2 2023-10-03 17:28:43.001953 -0.039037
3 2023-10-03 17:28:43.002930 -0.029386
4 2023-10-03 17:28:43.003906 -0.021782

Timestamp         X         Y          Z  Magnitude
0 2023-10-03 17:28:43.000000  0.567907 -0.876585  10.160894  10.214435
1 2023-10-03 17:28:43.031250  0.567907 -0.876585  10.160894  10.214435
2 2023-10-03 17:28:43.062500  0.567907 -0.876585  10.160894  10.214435
3 2023-10-03 17:28:43.093750  0.567907 -0.876585  10.256794  10.309837
4 2023-10-03 17:28:43.125000  0.567907 -0.876585  10.064994  10.119043

#### 2-b. Load Data of Other EEG Sources

In [56]:
file = 'sample_ecg.csv'
data = pd.read_csv(file)
data.head()

Timestamp        mV
0  2016-10-14 10:10:51.000000 -0.206620
1  2016-10-14 10:10:51.000977 -0.197554
2  2016-10-14 10:10:51.001953 -0.186148
3  2016-10-14 10:10:51.002930 -0.197847
4  2016-10-14 10:10:51.003906 -0.190243

### 3. Setup Data

Set the parameters of your data, such as the sampling rate `fs` (Hz) and segment size `seg_size` (seconds).

In [69]:
fs = 1024
seg_size = 60

Segment your data into 60-second windows.

In [70]:
data = heartview.segment_data(data, fs, seg_size)
data

Segment                  Timestamp        mV
0             1 2023-10-03 17:28:43.000000 -0.045764
1             1 2023-10-03 17:28:43.000977 -0.050443
2             1 2023-10-03 17:28:43.001953 -0.039037
3             1 2023-10-03 17:28:43.002930 -0.029386
4             1 2023-10-03 17:28:43.003906 -0.021782
...         ...                        ...       ...
307195        5 2023-10-03 17:33:42.995117  0.005124
307196        5 2023-10-03 17:33:42.996094  0.013313
307197        5 2023-10-03 17:33:42.997070  0.007756
307198        5 2023-10-03 17:33:42.998047  0.014483
307199        5 2023-10-03 17:33:42.999023  0.023549

[307200 rows x 3 columns]

### 4. Filter Data

Filter out any 60-Hz powerline interference, baseline wander, and muscle noise.

In [71]:
data['Powerline'] = ECG.powerline_int_filter(data['mV'], fs, q = 20, freq = 60)
data['Filtered'] = ECG.baseline_muscle_filter(data['Powerline'], 0.5, 45, fs, order = 4)
data.head()

Segment                  Timestamp        mV  Powerline  Filtered
0        1 2023-10-03 17:28:43.000000 -0.045764  -0.043125  0.018008
1        1 2023-10-03 17:28:43.000977 -0.050443  -0.048157  0.021933
2        1 2023-10-03 17:28:43.001953 -0.039037  -0.037414  0.025466
3        1 2023-10-03 17:28:43.002930 -0.029386  -0.028653  0.028245
4        1 2023-10-03 17:28:43.003906 -0.021782  -0.022051  0.029948

### 5. Assess Signal Quality

##### First, detect the number of peaks (i.e., heartbeats) in each segment of the signal. Save each peak occurrence in a `Peak` column in the data frame.

In [72]:
peak_ix = ECG.detect_rpeaks(data, 'Filtered', fs)
data.loc[peak_ix, 'Peak'] = 1
data.head()

Segment                  Timestamp        mV  Powerline  Filtered  Peak
0        1 2023-10-03 17:28:43.000000 -0.045764  -0.043125  0.018008   NaN
1        1 2023-10-03 17:28:43.000977 -0.050443  -0.048157  0.021933   NaN
2        1 2023-10-03 17:28:43.001953 -0.039037  -0.037414  0.025466   NaN
3        1 2023-10-03 17:28:43.002930 -0.029386  -0.028653  0.028245   NaN
4        1 2023-10-03 17:28:43.003906 -0.021782  -0.022051  0.029948   NaN

We can quickly verify that peaks have been detected.

In [73]:
data['Peak'].sum()

1213.0

##### Compute second-by-second mean heart rate (HR) and interbeat interval (IBI) values and label all invalid values.

In [74]:
interval_data = ECG.get_seconds(data, 'Peak', fs, seg_size)
interval_data

Segment  Second           Timestamp      Mean HR    Mean IBI  # R Peaks  \
0          1       1 2023-10-03 17:28:43          NaN         NaN        1.0   
1          1       2 2023-10-03 17:28:44  1159.245283   51.757812        0.0   
2          1       3 2023-10-03 17:28:45   418.671210  143.310547        2.0   
3          1       4 2023-10-03 17:28:46   337.170732  177.951389        7.0   
4          1       5 2023-10-03 17:28:47   307.969925  194.824219        3.0   
..       ...     ...                 ...          ...         ...        ...   
295        5     296 2023-10-03 17:33:38   319.445407  187.825521        5.0   
296        5     297 2023-10-03 17:33:39   368.640000  162.760417        5.0   
297        5     298 2023-10-03 17:33:40   218.259325  274.902344        5.0   
298        5     299 2023-10-03 17:33:41   261.632363  229.329427        2.0   
299        6     300 2023-10-03 17:33:42   347.609618  172.607422        5.0   

     Invalid  
0          0  
1          1  
2          1  
3          1  
4          1  
..       ...  
295        1  
296        1  
297        0  
298        1  
299        1  

[300 rows x 7 columns]

##### Compute the SQA metrics by segment.

In [75]:
peaks_by_seg = SQA.evaluate_peaks(interval_data, seg_size)
peaks_by_seg.head()

Segment           Timestamp  Detected    Expected
0       1 2023-10-03 17:28:43     253.0  288.000000
1       2 2023-10-03 17:29:43     242.0  265.295711
2       3 2023-10-03 17:30:43     272.0  282.299692
3       4 2023-10-03 17:31:43     257.0  266.420859
4       5 2023-10-03 17:32:43     189.0  286.911274

In [76]:
sqa = SQA.compute_metrics(peaks_by_seg)
sqa

Segment           Timestamp  Detected    Expected  Invalid    Missing  \
0       1 2023-10-03 17:28:43     253.0  288.000000        1  35.000000   
1       2 2023-10-03 17:29:43     242.0  265.295711        1  23.295711   
2       3 2023-10-03 17:30:43     272.0  282.299692        1  10.299692   
3       4 2023-10-03 17:31:43     257.0  266.420859        1   9.420859   
4       5 2023-10-03 17:32:43     189.0  286.911274        0  97.911274   

   % Missing  
0  12.152778  
1   8.781036  
2   3.648496  
3   3.536082  
4  34.125977

## Visualize Data

##### Visualize the raw and filtered ECG signal during Segment 1.

In [77]:
heartview.plot_signal(data, 'Timestamp', ['mV', 'Filtered'], fs, seg_size, segment = 4, signal_type = 'ecg')

##### Visualize the expected-to-missing numbers of beats per segment.

In [78]:
SQA.plot_expected2missing(sqa, title = 'Sample ECG')